In [2]:
import pandas as pd
import plotly.express as px


#### Importieren der Datei

In [34]:
# Laden der Excel-Datei in ein Pandas Dataframe
df_psp = pd.read_excel('C:/Users/Ibrom/Studium/DLMDWME01/PSP_Jan_Feb_2019.xlsx', sheet_name='Sheet1')

# Umbenennen der ersten Spalte in 'Id'
df_psp = df_psp.rename(columns={df_psp.columns[0]: 'Id'})

df_psp.head()

Id                tmsp  country  amount  success         PSP  3D_secured  \
0   0 2019-01-01 00:01:11  Germany      89        0     UK_Card           0   
1   1 2019-01-01 00:01:17  Germany      89        1     UK_Card           0   
2   2 2019-01-01 00:02:49  Germany     238        0     UK_Card           1   
3   3 2019-01-01 00:03:13  Germany     238        1     UK_Card           1   
4   4 2019-01-01 00:04:33  Austria     124        0  Simplecard           0   

     card  
0    Visa  
1    Visa  
2  Diners  
3  Diners  
4  Diners

#### Allgemeine Informationen zum Datensatz

In [4]:
# Anzahl der Spalten
num_cols = len(df_psp.columns)
print(f"Die Anzahl der Spalten ist: {num_cols}")

Die Anzahl der Spalten ist: 8


In [5]:
# Namen der Spalten
col_names = df_psp.columns.tolist()
print(f"Die Namen der Spalten sind: {col_names}")

Die Namen der Spalten sind: ['Id', 'tmsp', 'country', 'amount', 'success', 'PSP', '3D_secured', 'card']


In [6]:
# Datentypen der Spalten
col_types = df_psp.dtypes
print(f"Die Datentypen der Spalten sind: \n {col_types}")

Die Datentypen der Spalten sind: 
 Id                     int64
tmsp          datetime64[ns]
country               object
amount                 int64
success                int64
PSP                   object
3D_secured             int64
card                  object
dtype: object


In [7]:
# Mindest und Maximalwert der Spalten mit dem Namen 
# (angenommen, es bezieht sich auf die numerischen Spalten)
min_max_values = df_psp.describe().loc[['min','max']]
print(f"Mindest- und Maximalwerte der numerischen Spalten sind: \n {min_max_values}")

Mindest- und Maximalwerte der numerischen Spalten sind: 
           Id                 tmsp  amount  success  3D_secured
min      0.0  2019-01-01 00:01:11     6.0      0.0         0.0
max  50409.0  2019-02-28 23:48:19   630.0      1.0         1.0


In [8]:
# Anzahl der Zeilen
num_rows = len(df_psp)
print(f"Die Anzahl der Zeilen ist: {num_rows}")

Die Anzahl der Zeilen ist: 50410


#### Untersuchen des Merkmals "tmsp"

In [25]:
# Erstelle einen neuen DataFrame für 'tmsp'
df_tmsp = df_psp_tmsp_date.groupby('tmsp')['Id'].nunique().reset_index()
df_tmsp.columns = ['tmsp', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_tmsp, x="tmsp", y="count", title="Balkendiagramm für 'tmsp'")
fig.show()

In [26]:
# Konvertieren Sie die 'tmsp' Spalte zu datetime, falls noch nicht geschehen
df_psp['tmsp'] = pd.to_datetime(df_psp['tmsp'])

# Erstellen Sie einen vollständigen Datumsbereich für den gegebenen Zeitraum
date_range = pd.date_range(start='2019-01-01', end='2019-02-28')

# Finden Sie die fehlenden Daten heraus
missing_dates = date_range.difference(df_psp['tmsp'].dt.normalize()).tolist()

print("Fehlende Daten:", missing_dates)

Fehlende Daten: []


In [32]:
from datetime import timedelta

# Stelle sicher, dass 'tmsp' eine datetime Spalte ist
df_psp['tmsp'] = pd.to_datetime(df_psp['tmsp'])

# Sortiere df_psp nach 'tmsp'
df_psp_sorted = df_psp.sort_values(by='tmsp')

# Berechne den zeitlichen Abstand zwischen aufeinanderfolgenden Einträgen
df_psp_sorted['time_diff'] = df_psp_sorted['tmsp'].diff().dt.total_seconds()

# Entferne NaN-Werte und konvertiere den Abstand in Sekunden zu einem timedelta
df_psp_sorted['time_diff_timedelta'] = df_psp_sorted['time_diff'].dropna().apply(lambda x: timedelta(seconds=int(x)))

# Entferne die erste Zeile, die NaN-Werte enthält
df_psp_sorted = df_psp_sorted.iloc[1:, :]

# Erstelle ein neues DataFrame mit den gewünschten Spalten
df_time_diffs = pd.DataFrame({
    "Erste Zeile": df_psp_sorted.index[:-1],
    "Zweite Zeile": df_psp_sorted.index[1:],
    "tmsp erste Zeile": df_psp_sorted['tmsp'].values[:-1],
    "tmsp zweite Zeile": df_psp_sorted['tmsp'].values[1:],
    "Abstand [Sekunden]": df_psp_sorted['time_diff'].values[1:],
    "Abstand [Time]": df_psp_sorted['time_diff_timedelta'].values[1:]
})

# Sortiere nach "Abstand [Sekunden]" absteigend
df_time_diffs = df_time_diffs.sort_values(by="Abstand [Sekunden]", ascending=False)

df_time_diffs.head(5)

Erste Zeile  Zweite Zeile    tmsp erste Zeile   tmsp zweite Zeile  \
41266        41267         41268 2019-02-17 09:41:07 2019-02-17 10:03:15   
22534        22535         22536 2019-01-27 05:08:42 2019-01-27 05:28:11   
25531        25532         25533 2019-01-31 00:40:29 2019-01-31 00:59:08   
5551          5552          5553 2019-01-06 03:54:19 2019-01-06 04:12:50   
19511        19512         19513 2019-01-23 03:01:12 2019-01-23 03:19:33   

       Abstand [Sekunden]  Abstand [Time]  
41266              1328.0 0 days 00:22:08  
22534              1169.0 0 days 00:19:29  
25531              1119.0 0 days 00:18:39  
5551               1111.0 0 days 00:18:31  
19511              1101.0 0 days 00:18:21

In [30]:
# Berechne den Mittelwert
mean = df_time_diffs['Abstand [Sekunden]'].mean()

# Berechne die Standardabweichung
std_dev = df_time_diffs['Abstand [Sekunden]'].std()

# Berechne die Varianz
variance = df_time_diffs['Abstand [Sekunden]'].var()

print(f"Mittelwert: {mean}, Standardabweichung: {std_dev}, Varianz: {variance}")

Mittelwert: 101.1113712109189, Standardabweichung: 104.14722811449009, Varianz: 10846.645123931634


#### Untersuchen des Merkmals "country"

In [19]:
# Einzigartige Werte in 'country'
unique_countries = df_psp['country'].unique()

print("Einzigartige Länder:", unique_countries)

Einzigartige Länder: ['Germany' 'Austria' 'Switzerland']


In [20]:
# Erstelle einen neuen DataFrame für 'country'
df_country = df_psp_tmsp_date.groupby('country')['Id'].nunique().reset_index()
df_country.columns = ['country', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_country, x="country", y="count", title="Balkendiagramm für 'country'")
fig.show()

In [38]:
# Erstellen Sie eine Kopie von df_psp und konvertieren Sie die 'tmsp' Spalte zu datetime
df_psp_time = df_psp.copy()
df_psp_time['tmsp'] = pd.to_datetime(df_psp_time['tmsp'])

# Abrunden der 'tmsp' Werte auf die nächstgelegenen 15-Minuten-Intervalle
df_psp_time['time'] = df_psp_time['tmsp'].dt.round('15min').dt.time

# Ändern Sie 'success' in einen kategorischen Typ
df_psp_time['country'] = df_psp_time['country'].astype('category')

# Gruppieren Sie nach 'time' und 'success', und zählen Sie die einzigartige Anzahl von 'Id'
df_grouped = df_psp_time.groupby(['time', 'country'])['Id'].nunique().reset_index()
df_grouped.columns = ['time', 'country', 'count']

# Erstellen Sie das Balkendiagramm
fig = px.bar(df_grouped, x='time', y='count', color='country', title="Balkendiagramm für 'country'")
fig.update_layout(barmode='group')
fig.show()

#### Untersuchen des Merkmals "amount"

In [21]:
# Erstelle einen neuen DataFrame für 'amount'
df_amount = df_psp_tmsp_date.groupby('amount')['Id'].nunique().reset_index()
df_amount.columns = ['amount', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_amount, x="amount", y="count", title="Balkendiagramm für 'amount'")
fig.show()

#### Untersuchen des Merkmals "success"

In [24]:
# Erstelle einen neuen DataFrame für 'success'
df_success = df_psp_tmsp_date.groupby('success')['Id'].nunique().reset_index()
df_success.columns = ['success', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_success, x="success", y="count", title="Balkendiagramm für 'success'")
fig.show()

In [23]:
# Erstellen Sie eine Kopie von df_psp und konvertieren Sie die 'tmsp' Spalte zu datetime
df_psp_time = df_psp.copy()
df_psp_time['tmsp'] = pd.to_datetime(df_psp_time['tmsp'])

# Abrunden der 'tmsp' Werte auf die nächstgelegenen 15-Minuten-Intervalle
df_psp_time['time'] = df_psp_time['tmsp'].dt.round('15min').dt.time

# Ändern Sie 'success' in einen kategorischen Typ
df_psp_time['success'] = df_psp_time['success'].astype('category')

# Gruppieren Sie nach 'time' und 'success', und zählen Sie die einzigartige Anzahl von 'Id'
df_grouped = df_psp_time.groupby(['time', 'success'])['Id'].nunique().reset_index()
df_grouped.columns = ['time', 'success', 'count']

# Erstellen Sie das Balkendiagramm
fig = px.bar(df_grouped, x='time', y='count', color='success', title="Balkendiagramm für 'success'")
fig.update_layout(barmode='group')
fig.show()

In [39]:
# Erstellen Sie eine Kopie von df_psp und konvertieren Sie die 'tmsp' Spalte zu datetime
df_psp_time = df_psp.copy()
df_psp_time['tmsp'] = pd.to_datetime(df_psp_time['tmsp'])

# Abrunden der 'tmsp' Werte auf die nächstgelegenen 15-Minuten-Intervalle
df_psp_time['time'] = df_psp_time['tmsp'].dt.round('15min').dt.time

# Ändern Sie 'success' in einen kategorischen Typ
df_psp_time['success'] = df_psp_time['success'].astype('category')

countries = ["Germany", "Austria", "Switzerland"]

for country in countries:
    # Filtern Sie den DataFrame nach dem Land
    df_country = df_psp_time[df_psp_time['country'] == country]

    # Gruppieren Sie nach 'time' und 'success', und zählen Sie die einzigartige Anzahl von 'Id'
    df_grouped = df_country.groupby(['time', 'success'])['Id'].nunique().reset_index()
    df_grouped.columns = ['time', 'success', 'count']

    # Erstellen Sie das Balkendiagramm
    fig = px.bar(df_grouped, x='time', y='count', color='success', title=f"Balkendiagramm für 'success' in {country}")
    fig.update_layout(barmode='group')
    fig.show()

In [43]:
# Erstellen Sie eine Kopie von df_psp und konvertieren Sie die 'tmsp' Spalte zu datetime
df_psp_time = df_psp.copy()
df_psp_time['tmsp'] = pd.to_datetime(df_psp_time['tmsp'])

# Abrunden der 'tmsp' Werte auf die nächstgelegenen 15-Minuten-Intervalle
df_psp_time['time'] = df_psp_time['tmsp'].dt.round('15min').dt.time

# Ändern Sie 'success' in einen kategorischen Typ
df_psp_time['success'] = df_psp_time['success'].astype('category')

PSPs = ["UK_Card", "Simplecard", "Moneycard", "Goldcard"]

for PSP in PSPs:
    # Filtern Sie den DataFrame nach dem Land
    df_PSP = df_psp_time[df_psp_time['PSP'] == PSP]

    # Gruppieren Sie nach 'time' und 'success', und zählen Sie die einzigartige Anzahl von 'Id'
    df_grouped = df_PSP.groupby(['time', 'success'])['Id'].nunique().reset_index()
    df_grouped.columns = ['time', 'success', 'count']

    # Erstellen Sie das Balkendiagramm
    fig = px.bar(df_grouped, x='time', y='count', color='success', title=f"Balkendiagramm für 'success' in {PSP}")
    fig.update_layout(barmode='group')
    fig.show()

#### Untersuchen des Merkmals "PSP"

In [40]:
# Einzigartige Werte in 'country'
unique_PSP = df_psp['PSP'].unique()

print("Einzigartige PSP:", unique_PSP)

Einzigartige PSP: ['UK_Card' 'Simplecard' 'Moneycard' 'Goldcard']


In [ ]:
# Erstelle einen neuen DataFrame für 'PSP'
df_PSP = df_psp_tmsp_date.groupby('PSP')['Id'].nunique().reset_index()
df_PSP.columns = ['PSP', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_PSP, x="PSP", y="count", title="Balkendiagramm für 'PSP'")
fig.show()

#### Untersuchen des Merkmals "3D_secured"

In [ ]:
# Erstelle einen neuen DataFrame für '3D_secured'
df_3D_secured = df_psp_tmsp_date.groupby('3D_secured')['Id'].nunique().reset_index()
df_3D_secured.columns = ['3D_secured', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_3D_secured, x="3D_secured", y="count", title="Balkendiagramm für '3D_secured'")
fig.show()

#### Untersuchen des Merkmals "card"

In [ ]:
# Erstelle einen neuen DataFrame für '3D_secured'
df_card = df_psp_tmsp_date.groupby('card')['Id'].nunique().reset_index()
df_card.columns = ['card', 'count']

# Erstelle das Balkendiagramm
fig = px.bar(df_card, x="card", y="count", title="Balkendiagramm für 'card'")
fig.show()

### Ausreißer Analyse mit PyOD

In [59]:
from pyod.models.ecod import ECOD

# Wählen Sie die numerischen Spalten aus
df_psp_numerical_ECOD = df_psp[["Id", "amount", "success"]]

# Instanziieren Sie das ECOF-Modell
clf = ECOD(contamination=0.01)  # setze den Anteil der Ausreißer auf 1%

# Führe die Modellanpassung aus
clf.fit(df_psp_numerical_ECOD)

# Berechne die Ausreißerwahrscheinlichkeit für jeden Datenpunkt
scores_pred = clf.decision_function(df_psp_numerical_ECOD)

# Klassifiziere die Datenpunkte als inliers (1) oder outliers (-1)
y_pred = clf.predict(df_psp_numerical_ECOD)

# Erstelle einen neuen DataFrame und füge die Ausreißerwahrscheinlichkeit und die Klassifikation hinzu
df_psp_outliers_ECOD = df_psp.copy()
df_psp_outliers_ECOD['outlier_score'] = scores_pred
df_psp_outliers_ECOD['outlier'] = y_pred
df_psp_outliers_ECOD.head()

Id                tmsp  country  amount  success         PSP  3D_secured  \
0   0 2019-01-01 00:01:11  Germany      89        0     UK_Card           0   
1   1 2019-01-01 00:01:17  Germany      89        1     UK_Card           0   
2   2 2019-01-01 00:02:49  Germany     238        0     UK_Card           1   
3   3 2019-01-01 00:03:13  Germany     238        1     UK_Card           1   
4   4 2019-01-01 00:04:33  Austria     124        0  Simplecard           0   

     card  outlier_score  outlier  
0    Visa      13.062847        1  
1    Visa      13.737990        1  
2  Diners      10.994345        1  
3  Diners      12.074953        1  
4  Diners      10.953669        1

In [60]:
df_psp_outliers_ECOD.sort_values("outlier_score", ascending=False)

Id                tmsp      country  amount  success        PSP  \
50409  50409 2019-02-28 23:48:19      Austria      91        1  Moneycard   
50397  50397 2019-02-28 23:31:08  Switzerland      23        1    UK_Card   
1          1 2019-01-01 00:01:17      Germany      89        1    UK_Card   
50405  50405 2019-02-28 23:45:39  Switzerland     415        0    UK_Card   
50404  50404 2019-02-28 23:45:39  Switzerland     415        0    UK_Card   
...      ...                 ...          ...     ...      ...        ...   
24954  24954 2019-01-30 07:35:38  Switzerland     200        0  Moneycard   
24895  24895 2019-01-30 05:37:56      Germany     201        0    UK_Card   
24896  24896 2019-01-30 05:38:15      Germany     201        0    UK_Card   
24897  24897 2019-01-30 05:38:25      Germany     201        0    UK_Card   
25418  25418 2019-01-30 21:25:39      Austria     201        0    UK_Card   

       3D_secured    card  outlier_score  outlier  
50409           0  Master      14.400863        1  
50397           0    Visa      14.011439        1  
1               0    Visa      13.737990        1  
50405           0    Visa      13.625534        1  
50404           0    Visa      13.443212        1  
...           ...     ...            ...      ...  
24954           0    Visa       1.626371        0  
24895           1  Master       1.622073        0  
24896           1  Master       1.622033        0  
24897           1  Master       1.621993        0  
25418           0  Diners       1.618224        0  

[50410 rows x 10 columns]

In [48]:
from pyod.models.knn import KNN
# Wählen Sie die numerischen Spalten aus
df_psp_numerical_KNN = df_psp[["Id", "amount", "success"]]

# Instanziieren Sie das KNN-Modell
clf = KNN(contamination=0.01)  # setze den Anteil der Ausreißer auf 1%

# Führe die Modellanpassung aus
clf.fit(df_psp_numerical_KNN)

# Berechne die Ausreißerwahrscheinlichkeit für jeden Datenpunkt
scores_pred = clf.decision_function(df_psp_numerical_KNN)

# Klassifiziere die Datenpunkte als inliers (1) oder outliers (-1)
y_pred = clf.predict(df_psp_numerical_KNN)

# Erstelle einen neuen DataFrame und füge die Ausreißerwahrscheinlichkeit und die Klassifikation hinzu
df_psp_outliers_KNN = df_psp.copy()
df_psp_outliers_KNN['outlier_score'] = scores_pred
df_psp_outliers_KNN['outlier'] = y_pred

In [53]:
df_psp_outliers_KNN.head()

Id                tmsp  country  amount  success         PSP  3D_secured  \
0   0 2019-01-01 00:01:11  Germany      89        0     UK_Card           0   
1   1 2019-01-01 00:01:17  Germany      89        1     UK_Card           0   
2   2 2019-01-01 00:02:49  Germany     238        0     UK_Card           1   
3   3 2019-01-01 00:03:13  Germany     238        1     UK_Card           1   
4   4 2019-01-01 00:04:33  Austria     124        0  Simplecard           0   

     card  outlier_score  outlier  
0    Visa      18.000000        0  
1    Visa      17.029386        0  
2  Diners      11.661904        0  
3  Diners      10.862780        0  
4  Diners      23.853721        0

In [61]:
df_psp_outliers_KNN.sort_values("outlier_score", ascending=False)

Id                tmsp  country  amount  success         PSP  \
28580  28580 2019-02-03 03:30:54  Germany     602        0   Moneycard   
30150  30150 2019-02-04 16:58:29  Austria     630        1   Moneycard   
44597  44597 2019-02-21 11:18:51  Austria     556        1    Goldcard   
44596  44596 2019-02-21 11:18:08  Austria     556        0     UK_Card   
7742    7742 2019-01-08 13:53:01  Germany     581        0     UK_Card   
...      ...                 ...      ...     ...      ...         ...   
36357  36357 2019-02-11 12:27:45  Germany     259        0     UK_Card   
36356  36356 2019-02-11 12:27:08  Germany     259        0     UK_Card   
6517    6517 2019-01-07 08:51:08  Germany     157        0     UK_Card   
36350  36350 2019-02-11 12:23:14  Germany      78        0  Simplecard   
1439    1439 2019-01-02 03:58:46  Germany      92        0     UK_Card   

       3D_secured    card  outlier_score  outlier  
28580           1  Master     243.248844        1  
30150           1    Visa     222.105831        1  
44597           0  Diners     192.203018        1  
44596           0  Diners     191.838474        1  
7742            0  Master     188.812076        1  
...           ...     ...            ...      ...  
36357           0  Diners       2.000000        0  
36356           0  Diners       2.000000        0  
6517            0  Master       2.000000        0  
36350           0  Master       2.000000        0  
1439            0    Visa       2.000000        0  

[50410 rows x 10 columns]

In [55]:
import plotly.graph_objects as go

# Erstelle ein Histogramm der outlier_score-Werte
fig = px.histogram(df_psp_outliers_KNN, x="outlier_score", title="Histogramm der outlier_score-Werte")
fig.show()

# Erstelle ein Streudiagramm von 'amount' gegen 'outlier_score'
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=df_psp_outliers_KNN['amount'],
    y=df_psp_outliers_KNN['outlier_score'],
    mode='markers',
    marker=dict(
        color=df_psp_outliers_KNN['outlier'],
        colorscale='Viridis',
        opacity=0.8,
        size=5
    ),
    text=df_psp_outliers_KNN.index,
))
fig.update_layout(title='Streudiagramm von amount gegen outlier_score', 
                  xaxis_title='amount', yaxis_title='outlier_score')
fig.show()

In [ ]:
import plotly.graph_objects as go

# Erstelle ein Scatterplot von 'amount' gegen 'outlier_score'
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=df_psp_outliers['amount'],
    y=df_psp_outliers['outlier_score'],
    mode='markers',
    marker=dict(
        color=df_psp_outliers['outlier'],
        colorscale='Viridis',
        opacity=0.8,
        size=5
    ),
    text=df_psp_outliers.index,
))
fig.update_layout(title='Scatterplot von amount gegen outlier_score', 
                  xaxis_title='amount', yaxis_title='outlier_score')
fig.show()

### Korrelationsanalyse